## pip install the transformers and datasets libraries.

In [1]:
!pip install datasets
!pip install transformers

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 486.2/486.2 kB 4.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 8.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.5/212.5 kB 8.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 11.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 16.1 MB/s eta 0:00:00
INFO: pip is looking at multiple versions of multiprocess to determine which version is compatible with other requirements. This could take a while.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.3/134.3 kB 4.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.4/7.4 MB 13.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 34.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 39.2 MB/s eta 0:00:00


In [4]:
model_name =  'distilbert-base-uncased' #'AI-Growth-Lab/PatentSBERTa'

##  Import relevant libraries and dependencies

In [5]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
# Pretty print
from pprint import pprint
# Datasets load_dataset function
from datasets import load_dataset
# Transformers Autokenizer
from transformers import AutoTokenizer, AutoModelForSequenceClassification, DistilBertForSequenceClassification
tokenizer = AutoTokenizer.from_pretrained(model_name)
# Standard PyTorch DataLoader
from torch.utils.data import DataLoader

from transformers import pipeline, Trainer, TrainingArguments

use the `load_dataset` function to load all the patent applications that were filed to the USPTO in January 2016. We specify the date ranges of the training and validation sets as January 1-21, 2016 and January 22-31, 2016, respectively.

In [7]:
dataset_dict = load_dataset('HUPD/hupd',
    name='sample',
    data_files="https://huggingface.co/datasets/HUPD/hupd/blob/main/hupd_metadata_2022-02-22.feather",
    icpr_label=None,
    train_filing_start_date='2016-01-01',
    train_filing_end_date='2016-01-21',
    val_filing_start_date='2016-01-22',
    val_filing_end_date='2016-01-31',
)

print('Loading is done!')

Loading dataset with config: PatentsConfig(name='sample', version=0.0.0, data_dir='sample', data_files={'train': ['https://huggingface.co/datasets/HUPD/hupd/blob/main/hupd_metadata_2022-02-22.feather']}, description='Patent data from January 2016, for debugging')


Using metadata file: /root/.cache/huggingface/datasets/downloads/bac34b767c2799633010fa78ecd401d2eeffd62eff58abdb4db75829f8932710


Reading metadata file: /root/.cache/huggingface/datasets/downloads/bac34b767c2799633010fa78ecd401d2eeffd62eff58abdb4db75829f8932710
Filtering train dataset by filing start date: 2016-01-01
Filtering train dataset by filing end date: 2016-01-21
Filtering val dataset by filing start date: 2016-01-22
Filtering val dataset by filing end date: 2016-01-31


Generating train split: 0 examples [00:00, ? examples/s]

Generating validation split: 0 examples [00:00, ? examples/s]

Dataset hupd downloaded and prepared to /root/.cache/huggingface/datasets/HUPD___hupd/sample-4345d0959024424b/0.0.0/6920d2def8fd7767046c0470603357f76866e5a09c97e19571896bfdca521142. Subsequent calls will reuse this data.


  0%|          | 0/2 [00:00<?, ?it/s]

Loading is done!


In [8]:
dataset_dict.shape

{'train': (16153, 14), 'validation': (9094, 14)}

In [9]:
validation_dict = dataset_dict['validation']
print(len(validation_dict))

9094


In [10]:
validation_dict[:1]

{'patent_number': ['13144833'],
 'decision': ['REJECTED'],
 'title': ['ROSACEA TREATMENTS AND KITS FOR PERFORMING THEM'],
 'abstract': ['Regimen for the treatment of rosacea include the application of an anti-redness composition to at least a portion of the cleansed area of skin afflicted with rosacea. The regimen may include the application of one or more of a polymetal complex, a composition containing metronidazole, and/or a protective composition. Kits containing components useful in performing such regimens are also described.'],
 'claims': ['1. A treatment regimen comprising: cleansing at least a portion of an area of skin afflicted with rosacea with an antimicrobial or cleanser; applying an anti-redness composition to at least a portion of the cleansed area; and applying a protective composition to at least a portion of the cleansed, and moisturized area. 2. A treatment regimen as in claim 1 further comprising the step of applying a composition containing metronidazole to at lea

In [17]:
keys = list(validation_dict[:1].keys())

In [18]:
keys

['patent_number',
 'decision',
 'title',
 'abstract',
 'claims',
 'background',
 'summary',
 'description',
 'cpc_label',
 'ipc_label',
 'filing_date',
 'patent_issue_date',
 'date_published',
 'examiner_id']

In [20]:
type(validation_dict[:1])

dict

## save to csv file

In [21]:
import csv

with open('patent_application.csv', 'w') as csvfile:
	writer = csv.DictWriter(csvfile, fieldnames = keys)
	writer.writeheader()
	writer.writerows([validation_dict[:1]])

In [22]:
import pandas as pd

df = pd.read_csv('patent_application.csv')

In [23]:
df

patent_number      decision  \
0  ['13144833']  ['REJECTED']   

                                               title  \
0  ['ROSACEA TREATMENTS AND KITS FOR PERFORMING T...   

                                            abstract  \
0  ['Regimen for the treatment of rosacea include...   

                                              claims  \
0  ['1. A treatment regimen comprising: cleansing...   

                                          background  \
0  ['<SOH> BACKGROUND <EOH>Rosacea is a chronic i...   

                                             summary  \
0  ['<SOH> SUMMARY <EOH>The present disclosure pr...   

                                         description     cpc_label  \
0  ["CROSS REFERENCE TO RELATED APPLICATION This ...  ['A61K3334']   

      ipc_label   filing_date patent_issue_date date_published  examiner_id  
0  ['A61K3334']  ['20160122']              ['']   ['20160630']  ['75390.0']